# initial setup

In [1]:
from __future__ import division
import os
import cv2
import numpy as np
import sys
import pickle
from optparse import OptionParser
import time
from keras_frcnn import config
from keras import backend as K
from keras.layers import Input
from keras.models import Model
from keras_frcnn import roi_helpers
from keras_frcnn.pascal_voc import pascal_voc_util
from keras_frcnn.pascal_voc_parser import get_data
from keras_frcnn import data_generators
import random 
from matplotlib import pyplot as plt

from utils import get_bbox

Using TensorFlow backend.


In [2]:
config_output_filename = "config.pickle"

with open(config_output_filename, 'rb') as f_in:
	C = pickle.load(f_in)
C.network = 'vgg16'
from keras_frcnn import vgg as nn

In [3]:
img_path = "./TEST/VOCdevkit"
# Method to transform the coordinates of the bounding box to its original size
def get_real_coordinates(ratio, x1, y1, x2, y2):
	real_x1 = int(round(x1 // ratio))
	real_y1 = int(round(y1 // ratio))
	real_x2 = int(round(x2 // ratio))
	real_y2 = int(round(y2 // ratio))

	return (real_x1, real_y1, real_x2 ,real_y2)
def format_img_size(img, C):
	""" formats the image size based on config """
	img_min_side = float(C.im_size)
	(height,width,_) = img.shape
		
	if width <= height:
		ratio = img_min_side/width
		new_height = int(ratio * height)
		new_width = int(img_min_side)
	else:
		ratio = img_min_side/height
		new_width = int(ratio * width)
		new_height = int(img_min_side)
	img = cv2.resize(img, (new_width, new_height), interpolation=cv2.INTER_CUBIC)
	return img, ratio	

def format_img_channels(img, C):
	""" formats the image channels based on config """
	img = img[:, :, (2, 1, 0)]
	img = img.astype(np.float32)
	img[:, :, 0] -= C.img_channel_mean[0]
	img[:, :, 1] -= C.img_channel_mean[1]
	img[:, :, 2] -= C.img_channel_mean[2]
	img /= C.img_scaling_factor
	img = np.transpose(img, (2, 0, 1))
	img = np.expand_dims(img, axis=0)
	return img

def format_img(img, C):
	""" formats an image for model prediction based on config """
	img, ratio = format_img_size(img, C)
	img = format_img_channels(img, C)
	return img, ratio

class_mapping = C.class_mapping


if 'bg' not in class_mapping:
	class_mapping['bg'] = len(class_mapping)

class_mapping = {v: k for k, v in class_mapping.items()}

class_to_color = {class_mapping[v]: np.random.randint(0, 255, 3) for v in class_mapping} #for every item, randomly select 3 integers from 0 to 255 (create random color )
C.num_rois = int(10)

num_features = 512
print(class_mapping)
print(class_to_color)

{0: 'chair', 1: 'car', 2: 'horse', 3: 'person', 4: 'bicycle', 5: 'cat', 6: 'dog', 7: 'train', 8: 'aeroplane', 9: 'diningtable', 10: 'tvmonitor', 11: 'bird', 12: 'bottle', 13: 'motorbike', 14: 'pottedplant', 15: 'boat', 16: 'sofa', 17: 'sheep', 18: 'cow', 19: 'bus', 20: 'bg'}
{'chair': array([200, 179, 248]), 'car': array([ 41, 221, 113]), 'horse': array([117, 118,  50]), 'person': array([118,  32,  36]), 'bicycle': array([ 61, 237, 162]), 'cat': array([205, 139, 170]), 'dog': array([82, 16, 13]), 'train': array([ 44, 142,  41]), 'aeroplane': array([ 60,  30, 103]), 'diningtable': array([171,  75, 163]), 'tvmonitor': array([208, 188, 144]), 'bird': array([193,  72,  27]), 'bottle': array([165, 197, 103]), 'motorbike': array([ 51,  53, 239]), 'pottedplant': array([217, 228, 124]), 'boat': array([191,  89, 122]), 'sofa': array([ 90,  52, 197]), 'sheep': array([164,  12,  59]), 'cow': array([168, 205, 166]), 'bus': array([ 83, 201, 205]), 'bg': array([157, 193,  25])}


In [4]:
! ls models

'ls' is not recognized as an internal or external command,
operable program or batch file.


In [5]:
C.model_path = "models/vgg/voc.hdf5"

# setup model

In [6]:
if K.image_dim_ordering() == 'th':
	input_shape_img = (3, None, None)
	input_shape_features = (num_features, None, None)
else:
	input_shape_img = (None, None, 3)
	input_shape_features = (None, None, num_features)


img_input = Input(shape=input_shape_img)
roi_input = Input(shape=(C.num_rois, 4))
feature_map_input = Input(shape=input_shape_features)

# define the base network (resnet here, can be VGG, Inception, etc)
shared_layers = nn.nn_base(img_input, trainable=True)

# define the RPN, built on the base layers
num_anchors = len(C.anchor_box_scales) * len(C.anchor_box_ratios)
rpn_layers = nn.rpn(shared_layers, num_anchors)

classifier = nn.classifier(feature_map_input, roi_input, C.num_rois, nb_classes=len(class_mapping), trainable=True)

model_rpn = Model(img_input, rpn_layers)
#model_classifier_only = Model([feature_map_input, roi_input], classifier)
model_classifier = Model([feature_map_input, roi_input], classifier)

# model loading
print('Loading weights from {}'.format(C.model_path))
model_rpn.load_weights(C.model_path, by_name=True)
model_classifier.load_weights(C.model_path, by_name=True)


model_rpn.compile(optimizer='sgd', loss='mse')
model_classifier.compile(optimizer='sgd', loss='mse')

all_imgs = []

classes = {}

bbox_threshold = 0.7

visualise = True








Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.
Loading weights from models/vgg/voc.hdf5









# set up dataset

In [7]:
# define pascal
DEVKIT_PATH = "./TEST/VOCdevkit"
SET = "test"
#pascal = pascal_voc_util(DEVKIT_PATH)

# define dataloader
all_imgs, classes_count, _ = get_data(DEVKIT_PATH) #run the VOC parser 
test_imgs = [s for s in all_imgs if s['imageset'] == SET]
if len(test_imgs) == 0:
    print(SET, " images not found. using trainval images for testing.")
    test_imgs = [s for s in all_imgs if s['imageset'] == 'trainval'] # for test purpose
    
print('Num val samples {}'.format(len(test_imgs)))
data_gen_val = data_generators.get_anchor_gt(test_imgs, classes_count, C, nn.get_img_output_length,K.image_dim_ordering(), mode='val')

img_pathes = [x["filepath"] for x in test_imgs]

# define detections
all_boxes = [[[] for _ in range(len(test_imgs))]
               for _ in range(21)]
empty_array = np.transpose(np.array([[],[],[],[],[]]), (1,0))

data path: ['./TEST/VOCdevkit\\VOC2007']
Parsing annotation files
[Errno 2] No such file or directory: './TEST/VOCdevkit\\VOC2007\\ImageSets\\Main\\trainval.txt'
Num val samples 4952


In [8]:
print(_)

{'dog': 0, 'person': 1, 'train': 2, 'sofa': 3, 'chair': 4, 'car': 5, 'pottedplant': 6, 'diningtable': 7, 'horse': 8, 'cat': 9, 'cow': 10, 'bus': 11, 'bicycle': 12, 'motorbike': 13, 'bird': 14, 'tvmonitor': 15, 'sheep': 16, 'aeroplane': 17, 'boat': 18, 'bottle': 19}


In [9]:
len(all_boxes[0])

4952

In [10]:
img_pathes

['./TEST/VOCdevkit\\VOC2007\\JPEGImages\\000001.jpg',
 './TEST/VOCdevkit\\VOC2007\\JPEGImages\\000002.jpg',
 './TEST/VOCdevkit\\VOC2007\\JPEGImages\\000003.jpg',
 './TEST/VOCdevkit\\VOC2007\\JPEGImages\\000004.jpg',
 './TEST/VOCdevkit\\VOC2007\\JPEGImages\\000006.jpg',
 './TEST/VOCdevkit\\VOC2007\\JPEGImages\\000008.jpg',
 './TEST/VOCdevkit\\VOC2007\\JPEGImages\\000010.jpg',
 './TEST/VOCdevkit\\VOC2007\\JPEGImages\\000011.jpg',
 './TEST/VOCdevkit\\VOC2007\\JPEGImages\\000013.jpg',
 './TEST/VOCdevkit\\VOC2007\\JPEGImages\\000014.jpg',
 './TEST/VOCdevkit\\VOC2007\\JPEGImages\\000015.jpg',
 './TEST/VOCdevkit\\VOC2007\\JPEGImages\\000018.jpg',
 './TEST/VOCdevkit\\VOC2007\\JPEGImages\\000022.jpg',
 './TEST/VOCdevkit\\VOC2007\\JPEGImages\\000025.jpg',
 './TEST/VOCdevkit\\VOC2007\\JPEGImages\\000027.jpg',
 './TEST/VOCdevkit\\VOC2007\\JPEGImages\\000028.jpg',
 './TEST/VOCdevkit\\VOC2007\\JPEGImages\\000029.jpg',
 './TEST/VOCdevkit\\VOC2007\\JPEGImages\\000031.jpg',
 './TEST/VOCdevkit\\VOC2007\

# infer data

In [11]:
image_index = sorted(img_pathes)


for idx, img_name in enumerate(image_index):
	if not img_name.lower().endswith(('.bmp', '.jpeg', '.jpg', '.png', '.tif', '.tiff')):
		continue
	print("inference image path:", img_name)
	st = time.time()
	filepath = img_name

	img = cv2.imread(filepath)

	X, ratio = format_img(img, C)
	img_scaled = (np.transpose(X[0,:,:,:],(1,2,0)) + 127.5).astype('uint8')

	if K.image_dim_ordering() == 'tf':
		X = np.transpose(X, (0, 2, 3, 1))

	# get the feature maps and output from the RPN
	[Y1, Y2, F] = model_rpn.predict(X)
	
    # infer roi
	R = roi_helpers.rpn_to_roi(Y1, Y2, C, K.image_dim_ordering(), overlap_thresh=0.8)
    # get bbox
#	all_dets, bboxes, probs = get_bbox(R, C, model_classifier, class_mapping, F, ratio, bbox_threshold=0.5)
    # convert from (x1,y1,x2,y2) to (x,y,w,h)
	R[:, 2] -= R[:, 0]
	R[:, 3] -= R[:, 1]

	# apply the spatial pyramid pooling to the proposed regions
	bboxes = {}
	probs = {}

	for jk in range(R.shape[0]//C.num_rois + 1):
		ROIs = np.expand_dims(R[C.num_rois*jk:C.num_rois*(jk+1), :], axis=0)
		if ROIs.shape[1] == 0:
			break

		if jk == R.shape[0]//C.num_rois:
			#pad R
			curr_shape = ROIs.shape
			target_shape = (curr_shape[0],C.num_rois,curr_shape[2])
			ROIs_padded = np.zeros(target_shape).astype(ROIs.dtype)
			ROIs_padded[:, :curr_shape[1], :] = ROIs
			ROIs_padded[0, curr_shape[1]:, :] = ROIs[0, 0, :]
			ROIs = ROIs_padded

		[P_cls, P_regr] = model_classifier.predict([F, ROIs])

		for ii in range(P_cls.shape[1]):

			if np.max(P_cls[0, ii, :]) < bbox_threshold or np.argmax(P_cls[0, ii, :]) == (P_cls.shape[2] - 1):
				#print("no boxes detected")
				continue
			cls_name = class_mapping[np.argmax(P_cls[0, ii, :])]

			if cls_name not in bboxes:
				bboxes[cls_name] = []
				probs[cls_name] = []

			(x, y, w, h) = ROIs[0, ii, :]

			cls_num = np.argmax(P_cls[0, ii, :])
			try:
				(tx, ty, tw, th) = P_regr[0, ii, 4*cls_num:4*(cls_num+1)]
				tx /= C.classifier_regr_std[0]
				ty /= C.classifier_regr_std[1]
				tw /= C.classifier_regr_std[2]
				th /= C.classifier_regr_std[3]
				x, y, w, h = roi_helpers.apply_regr(x, y, w, h, tx, ty, tw, th)
			except:
				pass
			bboxes[cls_name].append([C.rpn_stride*x, C.rpn_stride*y, C.rpn_stride*(x+w), C.rpn_stride*(y+h)])
			probs[cls_name].append(np.max(P_cls[0, ii, :]))
	
	for keyid in class_mapping:   
		key = class_mapping[keyid]
		if key not in bboxes or key == "bg":
			all_boxes[keyid][idx] = empty_array
			continue
		else:
			print("detections of ", key)
		if key == "bg":
			continue

		bbox = np.array(bboxes[key])

		new_boxes, new_probs = roi_helpers.non_max_suppression_fast(bbox, np.array(probs[key]), overlap_thresh=0.45)
		all_dets = []
		for jk in range(new_boxes.shape[0]):
			(x1, y1, x2, y2) = new_boxes[jk,:]
			(real_x1, real_y1, real_x2, real_y2) = get_real_coordinates(ratio, x1, y1, x2, y2)
			all_dets.append([real_x1, real_y1, real_x2, real_y2, new_probs[jk]])
		all_boxes[keyid][idx] = all_dets

inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000001.jpg
detections of  person
detections of  dog
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000002.jpg
detections of  train
detections of  pottedplant
detections of  boat
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000003.jpg
detections of  chair
detections of  pottedplant
detections of  boat
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000004.jpg
detections of  car
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000006.jpg
detections of  chair
detections of  person
detections of  pottedplant
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000008.jpg
detections of  chair
detections of  tvmonitor
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000010.jpg
detections of  horse
detections of  person
detections of  pottedplant
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000011.jpg
detections of  cat
detections of  dog
inference image path: ./TEST

detections of  person
detections of  bicycle
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000144.jpg
detections of  chair
detections of  person
detections of  diningtable
detections of  bottle
detections of  pottedplant
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000145.jpg
detections of  train
detections of  bus
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000148.jpg
detections of  bird
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000149.jpg
detections of  bottle
detections of  pottedplant
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000151.jpg
detections of  person
detections of  bottle
detections of  pottedplant
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000152.jpg
detections of  car
detections of  person
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000155.jpg
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000157.jpg
detections of  cat
detections of  sofa
inference image path: ./

detections of  chair
detections of  train
detections of  boat
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000283.jpg
detections of  person
detections of  bicycle
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000284.jpg
detections of  car
detections of  pottedplant
detections of  boat
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000286.jpg
detections of  person
detections of  pottedplant
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000287.jpg
detections of  person
detections of  pottedplant
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000290.jpg
detections of  cat
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000291.jpg
detections of  tvmonitor
detections of  pottedplant
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000292.jpg
detections of  cat
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000293.jpg
detections of  car
detections of  person
inference image path: ./TEST/VOCdevkit\VOC2007

detections of  chair
detections of  person
detections of  tvmonitor
detections of  bottle
detections of  pottedplant
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000415.jpg
detections of  car
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000418.jpg
detections of  person
detections of  aeroplane
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000421.jpg
detections of  tvmonitor
detections of  pottedplant
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000422.jpg
detections of  chair
detections of  person
detections of  dog
detections of  sofa
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000423.jpg
detections of  chair
detections of  person
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000425.jpg
detections of  car
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000426.jpg
detections of  bird
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000429.jpg
detections of  chair
inference image path: ./TEST

detections of  person
detections of  bicycle
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000566.jpg
detections of  person
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000567.jpg
detections of  person
detections of  bicycle
detections of  pottedplant
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000568.jpg
detections of  bird
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000569.jpg
detections of  bird
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000570.jpg
detections of  person
detections of  motorbike
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000571.jpg
detections of  tvmonitor
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000572.jpg
detections of  chair
detections of  bicycle
detections of  motorbike
detections of  pottedplant
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\000573.jpg
detections of  chair
detections of  person
detections of  bottle
detections of  pottedplant
inference

...

detections of  aeroplane
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009332.jpg
detections of  person
detections of  aeroplane
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009335.jpg
detections of  car
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009338.jpg
detections of  bicycle
detections of  motorbike
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009340.jpg
detections of  train
detections of  pottedplant
detections of  boat
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009341.jpg
detections of  car
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009344.jpg
detections of  person
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009345.jpg
detections of  person
detections of  pottedplant
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009346.jpg
detections of  cat
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009352.jpg
detections of  person
detections of  cat
detections of  dog
inf

detections of  chair
detections of  person
detections of  sofa
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009489.jpg
detections of  pottedplant
detections of  sheep
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009492.jpg
detections of  car
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009493.jpg
detections of  bicycle
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009495.jpg
detections of  motorbike
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009498.jpg
detections of  pottedplant
detections of  bus
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009501.jpg
detections of  train
detections of  pottedplant
detections of  boat
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009503.jpg
detections of  tvmonitor
detections of  sofa
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009505.jpg
detections of  horse
detections of  person
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009506.jpg

detections of  cat
detections of  dog
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009642.jpg
detections of  dog
detections of  pottedplant
detections of  sheep
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009643.jpg
detections of  pottedplant
detections of  boat
detections of  sheep
detections of  bus
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009645.jpg
detections of  bottle
detections of  pottedplant
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009646.jpg
detections of  cat
detections of  pottedplant
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009648.jpg
detections of  person
detections of  pottedplant
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009651.jpg
detections of  person
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009652.jpg
detections of  car
detections of  tvmonitor
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009653.jpg
detections of  person
inference image path: ./

detections of  person
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009784.jpg
detections of  train
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009786.jpg
detections of  cat
detections of  dog
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009787.jpg
detections of  chair
detections of  pottedplant
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009788.jpg
detections of  chair
detections of  bicycle
detections of  pottedplant
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009791.jpg
detections of  chair
detections of  train
detections of  tvmonitor
detections of  bus
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009793.jpg
detections of  pottedplant
detections of  boat
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009795.jpg
detections of  chair
detections of  person
detections of  tvmonitor
detections of  pottedplant
detections of  sofa
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009798.jpg


detections of  person
detections of  motorbike
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009925.jpg
detections of  pottedplant
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009927.jpg
detections of  car
detections of  bus
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009928.jpg
detections of  chair
detections of  bottle
detections of  pottedplant
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009929.jpg
detections of  pottedplant
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009930.jpg
detections of  chair
detections of  person
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009931.jpg
detections of  horse
detections of  person
detections of  train
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009933.jpg
detections of  cow
inference image path: ./TEST/VOCdevkit\VOC2007\JPEGImages\009934.jpg
detections of  aeroplane
detections of  bird
detections of  pottedplant
inference image path: ./TEST/VOCdevkit\VO

4952

In [12]:
for i in class_mapping.items():
    print(i)

(0, 'chair')
(1, 'car')
(2, 'horse')
(3, 'person')
(4, 'bicycle')
(5, 'cat')
(6, 'dog')
(7, 'train')
(8, 'aeroplane')
(9, 'diningtable')
(10, 'tvmonitor')
(11, 'bird')
(12, 'bottle')
(13, 'motorbike')
(14, 'pottedplant')
(15, 'boat')
(16, 'sofa')
(17, 'sheep')
(18, 'cow')
(19, 'bus')
(20, 'bg')


# evaluate accuracy

In [13]:
import xml.etree.ElementTree as ET 

In [14]:
# eval function
def voc_eval(detpath,
             annopath,
             imagesetfile,
             classname,
             cachedir,
             ovthresh=0.5,
             use_07_metric=False):
    """
    rec, prec, ap = voc_eval(detpath,
                                annopath,
                                imagesetfile,
                                classname,
                                [ovthresh],
                                [use_07_metric])
    Top level function that does the PASCAL VOC evaluation.
    detpath: Path to detections
        detpath.format(classname) should produce the detection results file.
    annopath: Path to annotations
        annopath.format(imagename) should be the xml annotations file.
    imagesetfile: Text file containing the list of images, one image per line.
    classname: Category name (duh)
    cachedir: Directory for caching the annotations
    [ovthresh]: Overlap threshold (default = 0.5)
    [use_07_metric]: Whether to use VOC07's 11 point AP computation
        (default False)
    """
    # assumes detections are in detpath.format(classname)
    # assumes annotations are in annopath.format(imagename)
    # assumes imagesetfile is a text file with each line an image name
    # cachedir caches the annotations in a pickle file

    # first load gt
    if not os.path.isdir(cachedir):
        os.mkdir(cachedir)
    cachefile = os.path.join(cachedir, '%s_annots.pkl' % imagesetfile)
    # read list of images
    with open(imagesetfile, 'r') as f:
        lines = f.readlines()

    imagenames = [x.strip() for x in lines]

    if not os.path.isfile(cachefile):
        # load annotations
        recs = {}
        for i, imagename in enumerate(imagenames):
            print(imagename)
            print(annopath.format(imagename))
            recs[imagename] = parse_rec(annopath.format(imagename))
            if i % 100 == 0:
                print('Reading annotation for {:d}/{:d}'.format(
                    i + 1, len(imagenames)))
        # save
        #print('Saving cached annotations to {:s}'.format(cachefile))
        # with open(cachefile, 'wb') as f:
        #  pickle.dump(recs, f)
    else:
        # load
        with open(cachefile, 'rb') as f:
            try:
                recs = pickle.load(f)
            except:
                recs = pickle.load(f, encoding='bytes')

    # extract gt objects for this class
    class_recs = {}
    npos = 0
    for imagename in imagenames:
        R = [obj for obj in recs[imagename] if obj['name'] == classname]
        bbox = np.array([x['bbox'] for x in R])
        difficult = np.array([x['difficult'] for x in R]).astype(np.bool)
        det = [False] * len(R)
        npos = npos + sum(~difficult)
        class_recs[imagename] = {'bbox': bbox,
                                 'difficult': difficult,
                                 'det': det}

    # read dets
    detfile = detpath.format(classname)
    with open(detfile, 'r') as f:
        lines = f.readlines()

    splitlines = [x.strip().split(' ') for x in lines]
    image_ids = [x[0] for x in splitlines]
    confidence = np.array([float(x[1]) for x in splitlines])
    BB = np.array([[float(z) for z in x[2:]] for x in splitlines])

    nd = len(image_ids)
    tp = np.zeros(nd)
    fp = np.zeros(nd)

    if BB.shape[0] > 0:
        # sort by confidence
        sorted_ind = np.argsort(-confidence)
#    sorted_scores = np.sort(-confidence)
        BB = BB[sorted_ind, :]
        image_ids = [image_ids[x] for x in sorted_ind]

        # go down dets and mark TPs and FPs
        for d in range(nd):
            id = image_ids[d][-10:-4]
            # catch bad detections
            try:
                R = class_recs[id]
            except:
                print("det not found")
                continue

            bb = BB[d, :].astype(float)
            ovmax = -np.inf
            BBGT = R['bbox'].astype(float)

            if BBGT.size > 0:
                # compute overlaps
                # intersection
                ixmin = np.maximum(BBGT[:, 0], bb[0])
                iymin = np.maximum(BBGT[:, 1], bb[1])
                ixmax = np.minimum(BBGT[:, 2], bb[2])
                iymax = np.minimum(BBGT[:, 3], bb[3])
                iw = np.maximum(ixmax - ixmin + 1., 0.)
                ih = np.maximum(iymax - iymin + 1., 0.)
                inters = iw * ih

                # union
                uni = ((bb[2] - bb[0] + 1.) * (bb[3] - bb[1] + 1.) +
                       (BBGT[:, 2] - BBGT[:, 0] + 1.) *
                       (BBGT[:, 3] - BBGT[:, 1] + 1.) - inters)

                overlaps = inters / uni
                ovmax = np.max(overlaps)
                jmax = np.argmax(overlaps)

            if ovmax > ovthresh:
                if not R['difficult'][jmax]:
                    if not R['det'][jmax]:
                        tp[d] = 1.
                        R['det'][jmax] = 1
                    else:
                        fp[d] = 1.
            else:
                fp[d] = 1.

    # compute precision recall
    fp = np.cumsum(fp)
    tp = np.cumsum(tp)
    rec = tp / float(npos)
    # avoid divide by zero in case the first detection matches a difficult
    # ground truth
    prec = tp / np.maximum(tp + fp, np.finfo(np.float64).eps)
    ap = voc_ap(rec, prec, use_07_metric)

    return rec, prec, ap


In [15]:
pascal_classes = np.asarray(['dog', 'cat', 'car', 'person', 'chair', 'bottle', 'diningtable', 'pottedplant', 'bird', 'horse', 'motorbike', 'bus', 'tvmonitor', 'sofa', 'boat', 'cow', 'aeroplane', 'train', 'sheep', 'bicycle', 'bg'])
PASCAL_CLASSES = pascal_classes

In [16]:
pascal_classes

array(['dog', 'cat', 'car', 'person', 'chair', 'bottle', 'diningtable',
       'pottedplant', 'bird', 'horse', 'motorbike', 'bus', 'tvmonitor',
       'sofa', 'boat', 'cow', 'aeroplane', 'train', 'sheep', 'bicycle',
       'bg'], dtype='<U11')

## write out detections to evaluate on official script

In [17]:
def get_voc_results_file_template(cls):
    # VOCdevkit/results/VOC2007/Main/<comp_id>_det_test_aeroplane.txt
    filename = 'det_' + "val" + '_'+cls+'.txt'
    filedir = os.path.join(DEVKIT_PATH, 'results', 'VOC2007', 'Main')
    if not os.path.exists(filedir):
        os.makedirs(filedir)
    path = os.path.join(filedir, filename)
    return path


def write_voc_results_file(pascal_classes, all_boxes, image_index):
    for cls_ind, cls in enumerate(pascal_classes):
        if cls == '__background__':
            continue
        print('Writing {} VOC results file'.format(cls))
        filename = get_voc_results_file_template(cls)
        with open(filename, 'wt') as f:
            for im_ind, index in enumerate(image_index):
                dets = np.asarray(all_boxes[cls_ind][im_ind])
                if dets == []:
                    continue
                # the VOCdevkit expects 1-based indices
                for k in range(dets.shape[0]):
                    f.write('{:s} {:.3f} {:.1f} {:.1f} {:.1f} {:.1f}\n'.
                            format(index, dets[k, -1],
                                   dets[k, 0] + 1, dets[k, 1] + 1,
                                   dets[k, 2] + 1, dets[k, 3] + 1))


def parse_rec(filename):
    """ Parse a PASCAL VOC xml file """
    tree = ET.parse(filename)
    objects = []
    for obj in tree.findall('object'):
        obj_struct = {}
        obj_struct['name'] = obj.find('name').text
        obj_struct['pose'] = obj.find('pose').text
        obj_struct['truncated'] = int(obj.find('truncated').text)
        obj_struct['difficult'] = int(obj.find('difficult').text)
        bbox = obj.find('bndbox')
        obj_struct['bbox'] = [int(bbox.find('xmin').text),
                              int(bbox.find('ymin').text),
                              int(bbox.find('xmax').text),
                              int(bbox.find('ymax').text)]
        objects.append(obj_struct)

    return objects


def voc_ap(rec, prec, use_07_metric=False):
    """ ap = voc_ap(rec, prec, [use_07_metric])
    Compute VOC AP given precision and recall.
    If use_07_metric is true, uses the
    VOC 07 11 point method (default:False).
    """
    if use_07_metric:
        # 11 point metric
        ap = 0.
        for t in np.arange(0., 1.1, 0.1):
            if np.sum(rec >= t) == 0:
                p = 0
            else:
                p = np.max(prec[rec >= t])
            ap = ap + p / 11.
    else:
        # correct AP calculation
        # first append sentinel values at the end
        mrec = np.concatenate(([0.], rec, [1.]))
        mpre = np.concatenate(([0.], prec, [0.]))

        # compute the precision envelope
        for i in range(mpre.size - 1, 0, -1):
            mpre[i - 1] = np.maximum(mpre[i - 1], mpre[i])

        # to calculate area under PR curve, look for points
        # where X axis (recall) changes value
        i = np.where(mrec[1:] != mrec[:-1])[0]

        # and sum (\Delta recall) * prec
        ap = np.sum((mrec[i + 1] - mrec[i]) * mpre[i + 1])
    return ap


In [18]:
write_voc_results_file(pascal_classes, all_boxes, image_index)

Writing dog VOC results file
Writing cat VOC results file
Writing car VOC results file
Writing person VOC results file


D:\Anaconda\envs\tf_gpu\lib\site-packages\ipykernel_launcher.py:20: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.


Writing chair VOC results file
Writing bottle VOC results file
Writing diningtable VOC results file
Writing pottedplant VOC results file
Writing bird VOC results file
Writing horse VOC results file
Writing motorbike VOC results file
Writing bus VOC results file
Writing tvmonitor VOC results file
Writing sofa VOC results file
Writing boat VOC results file
Writing cow VOC results file
Writing aeroplane VOC results file
Writing train VOC results file
Writing sheep VOC results file
Writing bicycle VOC results file
Writing bg VOC results file


# evaluate on VOC 2010 metric

In [19]:
def python_eval(output_dir='output'):
        annopath = os.path.join(DEVKIT_PATH, 'VOC2007','Annotations')
        annopath+='\\{:s}.xml'
       
        imagesetfile = os.path.join(
            DEVKIT_PATH,
            'VOC2007',
            'ImageSets',
            'Main',
            SET + '.txt')
    
        
        cachedir = os.path.join(DEVKIT_PATH, 'annotations_cache')
        aps = []
        # The PASCAL VOC metric changed in 2010.
        # VOC07 metric is quite old so don't use.
        use_07_metric = False
        print('VOC07 metric? ' + ('Yes' if use_07_metric else 'No'))
        if not os.path.isdir(output_dir):
            os.mkdir(output_dir)
        for i, cls in enumerate(PASCAL_CLASSES):
            if cls == 'bg':
                continue
            filename = get_voc_results_file_template(cls)
            print("filename")
            print(filename)
            rec, prec, ap = voc_eval(
                filename, annopath, imagesetfile, cls, cachedir, ovthresh=0.5,
                use_07_metric=use_07_metric)
            aps += [ap]
            print('AP for {} = {:.4f}'.format(cls, ap))
            with open(os.path.join(output_dir, cls + '_pr.pkl'), 'wb') as f:
                pickle.dump({'rec': rec, 'prec': prec, 'ap': ap}, f)
        print('Mean AP = {:.4f}'.format(np.mean(aps)))
        print('~~~~~~~~')
        print('Results:')
        for ap in aps:
            print('{:.3f}'.format(ap))
        print('{:.3f}'.format(np.mean(aps)))
        print('~~~~~~~~')
        print('')
        print('--------------------------------------------------------------')
        print('Results computed with the **unofficial** Python eval code.')
        print('Results should be very close to the official MATLAB eval code.')
        print('Recompute with `./tools/reval.py --matlab ...` for your paper.')
        print('-- Thanks, The Management')
        print('--------------------------------------------------------------')

In [20]:
# evaluate detections
python_eval()

VOC07 metric? No
filename
./TEST/VOCdevkit\results\VOC2007\Main\det_val_dog.txt
000001
./TEST/VOCdevkit\VOC2007\Annotations\000001.xml
Reading annotation for 1/4952
000002
./TEST/VOCdevkit\VOC2007\Annotations\000002.xml
000003
./TEST/VOCdevkit\VOC2007\Annotations\000003.xml
000004
./TEST/VOCdevkit\VOC2007\Annotations\000004.xml
000006
./TEST/VOCdevkit\VOC2007\Annotations\000006.xml
000008
./TEST/VOCdevkit\VOC2007\Annotations\000008.xml
000010
./TEST/VOCdevkit\VOC2007\Annotations\000010.xml
000011
./TEST/VOCdevkit\VOC2007\Annotations\000011.xml
000013
./TEST/VOCdevkit\VOC2007\Annotations\000013.xml
000014
./TEST/VOCdevkit\VOC2007\Annotations\000014.xml
000015
./TEST/VOCdevkit\VOC2007\Annotations\000015.xml
000018
./TEST/VOCdevkit\VOC2007\Annotations\000018.xml
000022
./TEST/VOCdevkit\VOC2007\Annotations\000022.xml
000025
./TEST/VOCdevkit\VOC2007\Annotations\000025.xml
000027
./TEST/VOCdevkit\VOC2007\Annotations\000027.xml
000028
./TEST/VOCdevkit\VOC2007\Annotations\000028.xml
000029
./T

000986
./TEST/VOCdevkit\VOC2007\Annotations\000986.xml
000988
./TEST/VOCdevkit\VOC2007\Annotations\000988.xml
000990
./TEST/VOCdevkit\VOC2007\Annotations\000990.xml
000992
./TEST/VOCdevkit\VOC2007\Annotations\000992.xml
000994
./TEST/VOCdevkit\VOC2007\Annotations\000994.xml
000995
./TEST/VOCdevkit\VOC2007\Annotations\000995.xml
Reading annotation for 501/4952
000998
./TEST/VOCdevkit\VOC2007\Annotations\000998.xml
001000
./TEST/VOCdevkit\VOC2007\Annotations\001000.xml
001003
./TEST/VOCdevkit\VOC2007\Annotations\001003.xml
001005
./TEST/VOCdevkit\VOC2007\Annotations\001005.xml
001006
./TEST/VOCdevkit\VOC2007\Annotations\001006.xml
001007
./TEST/VOCdevkit\VOC2007\Annotations\001007.xml
001013
./TEST/VOCdevkit\VOC2007\Annotations\001013.xml
001016
./TEST/VOCdevkit\VOC2007\Annotations\001016.xml
001019
./TEST/VOCdevkit\VOC2007\Annotations\001019.xml
001020
./TEST/VOCdevkit\VOC2007\Annotations\001020.xml
001021
./TEST/VOCdevkit\VOC2007\Annotations\001021.xml
001022
./TEST/VOCdevkit\VOC2007\A

001956
./TEST/VOCdevkit\VOC2007\Annotations\001956.xml
001957
./TEST/VOCdevkit\VOC2007\Annotations\001957.xml
001959
./TEST/VOCdevkit\VOC2007\Annotations\001959.xml
001961
./TEST/VOCdevkit\VOC2007\Annotations\001961.xml
001965
./TEST/VOCdevkit\VOC2007\Annotations\001965.xml
001966
./TEST/VOCdevkit\VOC2007\Annotations\001966.xml
001967
./TEST/VOCdevkit\VOC2007\Annotations\001967.xml
001968
./TEST/VOCdevkit\VOC2007\Annotations\001968.xml
001969
./TEST/VOCdevkit\VOC2007\Annotations\001969.xml
001973
./TEST/VOCdevkit\VOC2007\Annotations\001973.xml
001974
./TEST/VOCdevkit\VOC2007\Annotations\001974.xml
001975
./TEST/VOCdevkit\VOC2007\Annotations\001975.xml
001979
./TEST/VOCdevkit\VOC2007\Annotations\001979.xml
001983
./TEST/VOCdevkit\VOC2007\Annotations\001983.xml
Reading annotation for 1001/4952
001984
./TEST/VOCdevkit\VOC2007\Annotations\001984.xml
001986
./TEST/VOCdevkit\VOC2007\Annotations\001986.xml
001987
./TEST/VOCdevkit\VOC2007\Annotations\001987.xml
001988
./TEST/VOCdevkit\VOC2007\

002983
./TEST/VOCdevkit\VOC2007\Annotations\002983.xml
002985
./TEST/VOCdevkit\VOC2007\Annotations\002985.xml
002991
./TEST/VOCdevkit\VOC2007\Annotations\002991.xml
002993
./TEST/VOCdevkit\VOC2007\Annotations\002993.xml
002996
./TEST/VOCdevkit\VOC2007\Annotations\002996.xml
002997
./TEST/VOCdevkit\VOC2007\Annotations\002997.xml
002998
./TEST/VOCdevkit\VOC2007\Annotations\002998.xml
002999
./TEST/VOCdevkit\VOC2007\Annotations\002999.xml
003001
./TEST/VOCdevkit\VOC2007\Annotations\003001.xml
003006
./TEST/VOCdevkit\VOC2007\Annotations\003006.xml
003010
./TEST/VOCdevkit\VOC2007\Annotations\003010.xml
003012
./TEST/VOCdevkit\VOC2007\Annotations\003012.xml
003014
./TEST/VOCdevkit\VOC2007\Annotations\003014.xml
003016
./TEST/VOCdevkit\VOC2007\Annotations\003016.xml
003018
./TEST/VOCdevkit\VOC2007\Annotations\003018.xml
Reading annotation for 1501/4952
003019
./TEST/VOCdevkit\VOC2007\Annotations\003019.xml
003020
./TEST/VOCdevkit\VOC2007\Annotations\003020.xml
003022
./TEST/VOCdevkit\VOC2007\

004002
./TEST/VOCdevkit\VOC2007\Annotations\004002.xml
004004
./TEST/VOCdevkit\VOC2007\Annotations\004004.xml
004006
./TEST/VOCdevkit\VOC2007\Annotations\004006.xml
004007
./TEST/VOCdevkit\VOC2007\Annotations\004007.xml
004018
./TEST/VOCdevkit\VOC2007\Annotations\004018.xml
004021
./TEST/VOCdevkit\VOC2007\Annotations\004021.xml
004022
./TEST/VOCdevkit\VOC2007\Annotations\004022.xml
004024
./TEST/VOCdevkit\VOC2007\Annotations\004024.xml
004026
./TEST/VOCdevkit\VOC2007\Annotations\004026.xml
004027
./TEST/VOCdevkit\VOC2007\Annotations\004027.xml
004029
./TEST/VOCdevkit\VOC2007\Annotations\004029.xml
004030
./TEST/VOCdevkit\VOC2007\Annotations\004030.xml
004032
./TEST/VOCdevkit\VOC2007\Annotations\004032.xml
004036
./TEST/VOCdevkit\VOC2007\Annotations\004036.xml
004038
./TEST/VOCdevkit\VOC2007\Annotations\004038.xml
004040
./TEST/VOCdevkit\VOC2007\Annotations\004040.xml
004041
./TEST/VOCdevkit\VOC2007\Annotations\004041.xml
004042
./TEST/VOCdevkit\VOC2007\Annotations\004042.xml
004043
./T

...

005357
./TEST/VOCdevkit\VOC2007\Annotations\005357.xml
005359
./TEST/VOCdevkit\VOC2007\Annotations\005359.xml
005361
./TEST/VOCdevkit\VOC2007\Annotations\005361.xml
005362
./TEST/VOCdevkit\VOC2007\Annotations\005362.xml
005364
./TEST/VOCdevkit\VOC2007\Annotations\005364.xml
005366
./TEST/VOCdevkit\VOC2007\Annotations\005366.xml
005372
./TEST/VOCdevkit\VOC2007\Annotations\005372.xml
005375
./TEST/VOCdevkit\VOC2007\Annotations\005375.xml
005376
./TEST/VOCdevkit\VOC2007\Annotations\005376.xml
005377
./TEST/VOCdevkit\VOC2007\Annotations\005377.xml
005381
./TEST/VOCdevkit\VOC2007\Annotations\005381.xml
005382
./TEST/VOCdevkit\VOC2007\Annotations\005382.xml
005386
./TEST/VOCdevkit\VOC2007\Annotations\005386.xml
005390
./TEST/VOCdevkit\VOC2007\Annotations\005390.xml
005392
./TEST/VOCdevkit\VOC2007\Annotations\005392.xml
005394
./TEST/VOCdevkit\VOC2007\Annotations\005394.xml
005399
./TEST/VOCdevkit\VOC2007\Annotations\005399.xml
005400
./TEST/VOCdevkit\VOC2007\Annotations\005400.xml
005401
./T

006491
./TEST/VOCdevkit\VOC2007\Annotations\006491.xml
006493
./TEST/VOCdevkit\VOC2007\Annotations\006493.xml
006494
./TEST/VOCdevkit\VOC2007\Annotations\006494.xml
006496
./TEST/VOCdevkit\VOC2007\Annotations\006496.xml
006498
./TEST/VOCdevkit\VOC2007\Annotations\006498.xml
006500
./TEST/VOCdevkit\VOC2007\Annotations\006500.xml
006502
./TEST/VOCdevkit\VOC2007\Annotations\006502.xml
006504
./TEST/VOCdevkit\VOC2007\Annotations\006504.xml
006505
./TEST/VOCdevkit\VOC2007\Annotations\006505.xml
006508
./TEST/VOCdevkit\VOC2007\Annotations\006508.xml
006510
./TEST/VOCdevkit\VOC2007\Annotations\006510.xml
006511
./TEST/VOCdevkit\VOC2007\Annotations\006511.xml
006513
./TEST/VOCdevkit\VOC2007\Annotations\006513.xml
006514
./TEST/VOCdevkit\VOC2007\Annotations\006514.xml
006516
./TEST/VOCdevkit\VOC2007\Annotations\006516.xml
006517
./TEST/VOCdevkit\VOC2007\Annotations\006517.xml
006518
./TEST/VOCdevkit\VOC2007\Annotations\006518.xml
006521
./TEST/VOCdevkit\VOC2007\Annotations\006521.xml
006522
./T

007532
./TEST/VOCdevkit\VOC2007\Annotations\007532.xml
007534
./TEST/VOCdevkit\VOC2007\Annotations\007534.xml
007539
./TEST/VOCdevkit\VOC2007\Annotations\007539.xml
007541
./TEST/VOCdevkit\VOC2007\Annotations\007541.xml
007542
./TEST/VOCdevkit\VOC2007\Annotations\007542.xml
007545
./TEST/VOCdevkit\VOC2007\Annotations\007545.xml
007548
./TEST/VOCdevkit\VOC2007\Annotations\007548.xml
007549
./TEST/VOCdevkit\VOC2007\Annotations\007549.xml
007550
./TEST/VOCdevkit\VOC2007\Annotations\007550.xml
007552
./TEST/VOCdevkit\VOC2007\Annotations\007552.xml
007553
./TEST/VOCdevkit\VOC2007\Annotations\007553.xml
007554
./TEST/VOCdevkit\VOC2007\Annotations\007554.xml
007556
./TEST/VOCdevkit\VOC2007\Annotations\007556.xml
007557
./TEST/VOCdevkit\VOC2007\Annotations\007557.xml
007560
./TEST/VOCdevkit\VOC2007\Annotations\007560.xml
007561
./TEST/VOCdevkit\VOC2007\Annotations\007561.xml
007562
./TEST/VOCdevkit\VOC2007\Annotations\007562.xml
007564
./TEST/VOCdevkit\VOC2007\Annotations\007564.xml
007567
./T

008554
./TEST/VOCdevkit\VOC2007\Annotations\008554.xml
008555
./TEST/VOCdevkit\VOC2007\Annotations\008555.xml
008560
./TEST/VOCdevkit\VOC2007\Annotations\008560.xml
008561
./TEST/VOCdevkit\VOC2007\Annotations\008561.xml
008563
./TEST/VOCdevkit\VOC2007\Annotations\008563.xml
008565
./TEST/VOCdevkit\VOC2007\Annotations\008565.xml
008566
./TEST/VOCdevkit\VOC2007\Annotations\008566.xml
008567
./TEST/VOCdevkit\VOC2007\Annotations\008567.xml
008569
./TEST/VOCdevkit\VOC2007\Annotations\008569.xml
008570
./TEST/VOCdevkit\VOC2007\Annotations\008570.xml
008571
./TEST/VOCdevkit\VOC2007\Annotations\008571.xml
008574
./TEST/VOCdevkit\VOC2007\Annotations\008574.xml
008575
./TEST/VOCdevkit\VOC2007\Annotations\008575.xml
008577
./TEST/VOCdevkit\VOC2007\Annotations\008577.xml
008578
./TEST/VOCdevkit\VOC2007\Annotations\008578.xml
008579
./TEST/VOCdevkit\VOC2007\Annotations\008579.xml
008580
./TEST/VOCdevkit\VOC2007\Annotations\008580.xml
008583
./TEST/VOCdevkit\VOC2007\Annotations\008583.xml
008589
./T

009592
./TEST/VOCdevkit\VOC2007\Annotations\009592.xml
009593
./TEST/VOCdevkit\VOC2007\Annotations\009593.xml
009594
./TEST/VOCdevkit\VOC2007\Annotations\009594.xml
009595
./TEST/VOCdevkit\VOC2007\Annotations\009595.xml
009599
./TEST/VOCdevkit\VOC2007\Annotations\009599.xml
009601
./TEST/VOCdevkit\VOC2007\Annotations\009601.xml
009602
./TEST/VOCdevkit\VOC2007\Annotations\009602.xml
009604
./TEST/VOCdevkit\VOC2007\Annotations\009604.xml
009606
./TEST/VOCdevkit\VOC2007\Annotations\009606.xml
009607
./TEST/VOCdevkit\VOC2007\Annotations\009607.xml
009608
./TEST/VOCdevkit\VOC2007\Annotations\009608.xml
009610
./TEST/VOCdevkit\VOC2007\Annotations\009610.xml
009612
./TEST/VOCdevkit\VOC2007\Annotations\009612.xml
009616
./TEST/VOCdevkit\VOC2007\Annotations\009616.xml
009622
./TEST/VOCdevkit\VOC2007\Annotations\009622.xml
009624
./TEST/VOCdevkit\VOC2007\Annotations\009624.xml
009625
./TEST/VOCdevkit\VOC2007\Annotations\009625.xml
009626
./TEST/VOCdevkit\VOC2007\Annotations\009626.xml
009628
./T

In [49]:
a = '../VOCdevkit/VOC2007/JPEGImages/000585.jpg'
a[-10:-4]

'000585'